## John Gabriel Cabatu-an
### CMSC 197 - 1
### lec 6

---

In [91]:
# importing
import numpy as np
import pandas as pd
import sklearn.model_selection
import sklearn.datasets
import os
import email
import math

# load data sets
dataset = sklearn.datasets.load_files(os.getcwd() + "/data",shuffle=False)
labels = pd.read_csv('labels', sep=" ")

with open('stop_words.txt', 'r') as file:
    stop_words = str(file.read()).split()


* preprocessing

In [92]:
def get_email_body(data):
    body = ""

    email_msg = email.message_from_bytes(data)
    if email_msg.is_multipart():
        for part in email_msg.walk():
            ctype = part.get_content_type()
            cdispo = str(part.get('Content-Disposition'))

            # skip any text/plain (txt) attachments
            if ctype == 'text/plain' and 'attachment' not in cdispo:
                body = part.get_payload(decode=True)  # decode
                break
    # not multipart - i.e. plain text, no attachments, keeping fingers crossed
    else:
        body = email_msg.get_payload(decode=True)

    words_list = str(body).lower().split()

    return [word for word in words_list if word not in stop_words and word.isalnum()]
    # return [word for word in words_list if word.isalnum()]

In [93]:
email_bodies = []

for data in dataset['data']:
    email_bodies.append(get_email_body(data))

# print(body.decode().split())
set_all = labels.copy()

set_all['email_msg'] = email_bodies
del set_all['dir']



* split data into three

In [94]:
set_train = set_all[:21301].copy()
set_train

email_type                                          email_msg
0            ham  [mailing, list, queried, weeks, ago, set, arch...
1           spam  [luxury, watches, buy, rolex, rolex, cartier, ...
2           spam  [qualifications, prestigious, redited, uni, kn...
3            ham  [verify, subscription, charter, members, signe...
4           spam  [chauncey, conferred, luscious, continued, ton...
...          ...                                                ...
21296       spam  [video, premiere, effects, audition, encore, d...
21297       spam                               [html, public, html]
21298        ham  [mounted, is1u60, infrared, demodulator, hb, r...
21299       spam  [depression, help, verified, collected, licens...
21300       spam  [hesitantly, derive, perverse, satisfaction, c...

[21301 rows x 2 columns]

In [95]:
set_test = set_all[21301:].copy()
set_test

email_type                                          email_msg
21301        ham  [things, perform, display, will, remain, scree...
21302       spam                     [offer, ialis, naax, limiited]
21303       spam  [ar, wne, cr, matter, ow, real, st, mmed, ia, ...
21304       spam  [video, premiere, effects, audition, encore, d...
21305       spam  [message, mime, bloodroot, freedom, gigavolt, ...
...          ...                                                ...
37817       spam  [news, expec, ventures, started, well, marketi...
37818       spam  [oil, sector, going, weekly, gift, kkpt, going...
37819       spam  [depression, help, verified, collected, licens...
37820       spam  [prosperous, increased, money, earning, respec...
37821       spam   [moat, coverall, cytochemistry, planeload, salk]

[16521 rows x 2 columns]

In [96]:
set_train_spam = set_train[set_train['email_type'] == 'spam']
set_train_spam

email_type                                          email_msg
1           spam  [luxury, watches, buy, rolex, rolex, cartier, ...
2           spam  [qualifications, prestigious, redited, uni, kn...
4           spam  [chauncey, conferred, luscious, continued, ton...
7           spam  [nbc, today, body, diet, magazines, will, thou...
8           spam  [oil, sector, going, weekly, gift, kkpt, going...
...          ...                                                ...
21295       spam                                                 []
21296       spam  [video, premiere, effects, audition, encore, d...
21297       spam                               [html, public, html]
21299       spam  [depression, help, verified, collected, licens...
21300       spam  [hesitantly, derive, perverse, satisfaction, c...

[13778 rows x 2 columns]

In [97]:
set_train_ham = set_train[set_train['email_type'] == 'ham']
set_train_ham

email_type                                          email_msg
0            ham  [mailing, list, queried, weeks, ago, set, arch...
3            ham  [verify, subscription, charter, members, signe...
5            ham                      [straw, poll, plan9, running]
6            ham  [working, departed, totally, bell, running, ha...
10           ham  [mass, acknowledgement, list, influx, 75, peop...
...          ...                                                ...
21270        ham  [equation, generate, prime, equation, theorem,...
21271        ham  [equation, generate, prime, equation, theorem,...
21288        ham  [dmdx, guidance, generating, dmdx, item, files...
21293        ham  [built, handyboard, works, testdigitals, remot...
21298        ham  [mounted, is1u60, infrared, demodulator, hb, r...

[7523 rows x 2 columns]

* get 10000 common words

In [98]:
word_count_train = {}
for body in set_train['email_msg']:
    for word in body:
        if word in word_count_train:
            word_count_train[word] += 1
        else:
            word_count_train[word] = 1

word_count_train = pd.DataFrame({'word': word_count_train.keys(), 'count': word_count_train.values()})
top_word_count_train = word_count_train.sort_values(by='count', ascending=False)[:10000]
top_word_count_train

word  count
49            will  10259
104           gold   3728
461        company   3534
508          board   3340
712              3   2999
...            ...    ...
22260          pd5      9
9534        binhex      9
31019   initialise      9
14790  wonderfully      9
6473           333      9

[10000 rows x 2 columns]

* Create Feature Matrices

In [99]:
set_matrix_spam = set_train_spam.copy()
for word in top_word_count_train['word'].values:
    temp = []
    for body in set_train_spam['email_msg']:
        if word in body:
            temp.append(1)
        else:
            temp.append(0)
    
    set_matrix_spam[word] = temp

/tmp/ipykernel_22240/173376633.py:10: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  set_matrix_spam[word] = temp
/tmp/ipykernel_22240/173376633.py:10: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  set_matrix_spam[word] = temp
/tmp/ipykernel_22240/173376633.py:10: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.c

In [100]:
set_matrix_spam

email_type                                          email_msg  will  \
1           spam  [luxury, watches, buy, rolex, rolex, cartier, ...     0   
2           spam  [qualifications, prestigious, redited, uni, kn...     0   
4           spam  [chauncey, conferred, luscious, continued, ton...     0   
7           spam  [nbc, today, body, diet, magazines, will, thou...     1   
8           spam  [oil, sector, going, weekly, gift, kkpt, going...     1   
...          ...                                                ...   ...   
21295       spam                                                 []     0   
21296       spam  [video, premiere, effects, audition, encore, d...     0   
21297       spam                               [html, public, html]     0   
21299       spam  [depression, help, verified, collected, licens...     0   
21300       spam  [hesitantly, derive, perverse, satisfaction, c...     0   

       gold  company  board  3  nil  time  list  ...  loud  multiplex  \
1         1        0      0  0    0     0     0  ...     0          0   
2         0        0      0  0    0     1     0  ...     0          0   
4         0        0      0  0    0     0     0  ...     0          0   
7         0        0      0  0    0     0     0  ...     0          0   
8         0        0      0  0    0     0     0  ...     0          0   
...     ...      ...    ... ..  ...   ...   ...  ...   ...        ...   
21295     0        0      0  0    0     0     0  ...     0          0   
21296     0        0      0  1    0     0     0  ...     0          0   
21297     0        0      0  0    0     0     0  ...     0          0   
21299     0        0      0  0    0     0     0  ...     0          0   
21300     0        0      0  0    0     0     0  ...     0          0   

       remnants  treating  gammoh  pd5  binhex  initialise  wonderfully  333  
1             0         0       0    0       0           0            0    0  
2             0         0       0    0       0           0            0    0  
4             0         0       0    0       0           0            0    0  
7             0         0       0    0       0           0            0    0  
8             0         0       0    0       0           0            0    0  
...         ...       ...     ...  ...     ...         ...          ...  ...  
21295         0         0       0    0       0           0            0    0  
21296         0         0       0    0       0           0            0    0  
21297         0         0       0    0       0           0            0    0  
21299         0         0       0    0       0           0            0    0  
21300         0         0       0    0       0           0            0    0  

[13778 rows x 10002 columns]

In [101]:
set_matrix_ham = set_train_ham.copy()
for word in top_word_count_train['word'].values:
    temp = []
    for body in set_train_ham['email_msg']:
        if word in body:
            temp.append(1)
        else:
            temp.append(0)
    
    set_matrix_ham[word] = temp
    

/tmp/ipykernel_22240/3518112718.py:10: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  set_matrix_ham[word] = temp
/tmp/ipykernel_22240/3518112718.py:10: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  set_matrix_ham[word] = temp
/tmp/ipykernel_22240/3518112718.py:10: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.

In [102]:
set_matrix_ham

email_type                                          email_msg  will  \
0            ham  [mailing, list, queried, weeks, ago, set, arch...     1   
3            ham  [verify, subscription, charter, members, signe...     0   
5            ham                      [straw, poll, plan9, running]     0   
6            ham  [working, departed, totally, bell, running, ha...     0   
10           ham  [mass, acknowledgement, list, influx, 75, peop...     0   
...          ...                                                ...   ...   
21270        ham  [equation, generate, prime, equation, theorem,...     0   
21271        ham  [equation, generate, prime, equation, theorem,...     0   
21288        ham  [dmdx, guidance, generating, dmdx, item, files...     1   
21293        ham  [built, handyboard, works, testdigitals, remot...     1   
21298        ham  [mounted, is1u60, infrared, demodulator, hb, r...     0   

       gold  company  board  3  nil  time  list  ...  loud  multiplex  \
0         0        0      0  0    0     0     1  ...     0          0   
3         0        0      0  0    0     0     0  ...     0          0   
5         0        0      0  0    0     0     0  ...     0          0   
6         0        0      0  0    0     0     1  ...     0          0   
10        0        0      0  0    0     0     1  ...     0          0   
...     ...      ...    ... ..  ...   ...   ...  ...   ...        ...   
21270     0        0      0  0    0     0     0  ...     0          0   
21271     0        0      0  0    0     0     0  ...     0          0   
21288     0        0      0  0    0     1     0  ...     0          0   
21293     0        0      0  1    0     0     0  ...     0          0   
21298     0        0      0  0    0     0     0  ...     0          0   

       remnants  treating  gammoh  pd5  binhex  initialise  wonderfully  333  
0             0         0       0    0       0           0            0    0  
3             0         0       0    0       0           0            0    0  
5             0         0       0    0       0           0            0    0  
6             0         0       0    0       0           0            0    0  
10            0         0       0    0       0           0            0    0  
...         ...       ...     ...  ...     ...         ...          ...  ...  
21270         0         0       0    0       0           0            0    0  
21271         0         0       0    0       0           0            0    0  
21288         0         0       0    0       0           0            0    0  
21293         0         0       0    0       0           0            0    0  
21298         0         0       0    0       0           0            0    0  

[7523 rows x 10002 columns]

* computing the priors

In [103]:
prior_spam = set_train_spam.count(axis=0)[0] / set_all.count(axis=0)[0]
prior_spam

0.3642853365765956

In [104]:
prior_ham = set_train_ham.count(axis=0)[0] / set_all.count(axis=0)[0]
prior_ham

0.19890539897414203

* computing the likelyhood of each word

In [105]:
prob_words_spam = {}
for i in top_word_count_train['word']:
    # equal to 1 because laplace smoothing
    prob_words_spam[i] = 0.05
    

for msg in set_train_spam['email_msg']:
    for word in msg:
        if word in prob_words_spam:
            prob_words_spam[word] += 1

total_word_spam = sum(prob_words_spam.values())

for e,i in enumerate(top_word_count_train['word']):
    prob_words_spam[i] /= total_word_spam

prob_words_spam

{'will': 0.012872090534470464,
 'gold': 0.00987829757489524,
 'company': 0.009108852144560975,
 'board': 0.0014360723603826667,
 '3': 0.0058251624911626314,
 'nil': 1.354657447771594e-07,
 'time': 0.0030481147232308634,
 'list': 0.0003794395511208235,
 '2': 0.0035520472938018965,
 'message': 0.001194943334679323,
 'help': 0.00149838660298016,
 'program': 0.0025414728377642875,
 '1998': 0.00012205463604422061,
 'send': 0.0008156392493032768,
 'microsoft': 0.004746855162736443,
 '1': 0.0017097131648325286,
 'number': 0.0030697892423952092,
 'info': 0.00434587655819605,
 'office': 0.004635773252019171,
 'good': 0.001541735641308851,
 'stock': 0.004806460090438392,
 'windows': 0.0036956409832656855,
 'find': 0.001181396760201607,
 'work': 0.00036860229153865074,
 'de': 0.0024168443525693006,
 'studies': 0.0002629390106124664,
 'read': 0.0020375402671932545,
 '1999': 9.767080198433192e-05,
 '8': 0.002666101322959274,
 'file': 0.0004065327000762554,
 'hb': 1.354657447771594e-07,
 '5': 0.0020

In [106]:
prob_words_ham = {}
for i in top_word_count_train['word']:
    prob_words_ham[i] = 0.05
    

for msg in set_train_ham['email_msg']:
    for word in msg:
        if word in prob_words_ham:
            prob_words_ham[word] += 1

total_word_ham = sum(prob_words_ham.values())

for e,i in enumerate(top_word_count_train['word']):
    prob_words_ham[i] /= total_word_ham

prob_words_ham

{'will': 0.012068867294063925,
 'gold': 0.0001797824205441027,
 'company': 0.000376984344358475,
 'board': 0.006157191844606409,
 '3': 0.0018603810379399198,
 'nil': 0.006455185862814794,
 'time': 0.003578228907611785,
 'list': 0.005710200817293832,
 '2': 0.002951565016379446,
 'message': 0.0048512768824579,
 'help': 0.004485357757157898,
 'program': 0.0030370191833656744,
 '1998': 0.004960833506799218,
 'send': 0.004112865234397417,
 'microsoft': 0.000571995135686021,
 '1': 0.0028967867042087874,
 'number': 0.0017683534734932126,
 'info': 0.0006552581701854225,
 'office': 0.000407660199174044,
 'good': 0.0028683019818800445,
 'stock': 0.00013157750583392283,
 'windows': 0.000902856141196801,
 'find': 0.0028661108493932184,
 'work': 0.003475245680730946,
 'de': 0.00176397120851956,
 'studies': 0.0034358052959680713,
 'read': 0.0018034115932824345,
 '1999': 0.0032999550817848374,
 '8': 0.0011614097746423112,
 'file': 0.002982240871195015,
 'hb': 0.0032780437569165737,
 '5': 0.0016215475

* making the email classifier

In [107]:
def score_spam(email_body):

    score = np.log(prior_spam)

    for word in email_body:
        if word in prob_words_spam:
            score += np.log(prob_words_spam[word])
    
    return score

In [108]:
def score_ham(email_body):

    score = np.log(prior_ham)

    for word in email_body:
        if word in prob_words_ham:
            score += np.log(prob_words_ham[word])
    
    return score

In [109]:
def is_spam(email_body):
    return np.exp(score_spam(email_body)) > np.exp(score_ham(email_body))

In [110]:
true_positive, true_negative, false_positive, false_negative = 0, 0, 0, 0

for test_email_type, test_email in zip(set_test['email_type'], set_test['email_msg']):
    res = 'spam' if is_spam(test_email) else 'ham'
    if res == 'spam':
        if res == test_email_type:
            true_negative += 1
        else:
            false_negative += 1
    else:
        if res == test_email_type:
            true_positive += 1
        else:
            false_positive += 1

true_positive, true_negative, false_positive, false_negative

(5117, 9278, 1856, 270)

In [111]:
acc = (true_negative+true_positive) / (true_negative+true_positive+false_negative+false_positive)
r = (true_positive) / (true_positive+false_negative)
p = (true_positive) / (true_positive+false_positive)

print(f'accuracy = {acc}\nrecall = {r}\nprecision = {p}')

accuracy = 0.8713152956842806
recall = 0.949879339149805
precision = 0.7338304890291123
